# Hapax legomena in parasha #5: Chayei Sarah (Genesis 23:1-25:18)

## Table of Content <a class="anchor" id="TOC"></a> (ToC)

* <a href="#bullet1">1 - Introduction</a>
* <a href="#bullet2">2 - Load Text-Fabric app and data</a>
* <a href="#bullet3">3 - Performing the queries</a>
* <a href="#bullet4">4 - Required libraries</a>
* <a href="#bullet5">5 - Further reading</a>
* <a href="#bullet6">6 - Notebook version details</a>

# 1 - Introduction <a class="anchor" id="bullet1"></a>
##### [Back to ToC](#TOC)

A *hapax legomenon* (ἅπαξ λεγόμενον) is the term used in linguistics and philology to refer to a word or expression that appears only once within a specific context. Usually, this context is defined as the entire works of an author or a well-defined corpus of literature. The term comes from Greek, where "hapax" means "once" and "legomenon" means "something said." In this Notebook, the context to determine the *hapax legomena* is the full text of the Tenach, or more precisely, the full Biblica Hebraica Stuttgartensia.

# 2 - Load Text-Fabric app and data <a class="anchor" id="bullet2"></a>
##### [Back to ToC](#TOC)

The following code will load the Text-Fabric version of the [Biblia Hebraica Stuttgartensia (Amstelodamensis)](https://etcbc.github.io/bhsa/) together with the additonal parasha related features from [tonyjurg/BHSaddons](https://github.com/tonyjurg/BHSaddons).

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
# Loading the Text-Fabric code
# Note: it is assumed Text-Fabric is installed in your environment.
from tf.fabric import Fabric
from tf.app import use

In [3]:
# load the app and data
BHSA = use ("etcbc/BHSA", version="2021", mod="tonyjurg/BHSaddons/tf/", hoist=globals())

**Locating corpus resources ...**

# 3 - Performing the queries <a class="anchor" id="bullet3"></a>
##### [Back to ToC](#TOC)

The Text-Fabric code in this Notebook first queries to find all word nodess for this parasha. The value for the feature freq_lex is then examined for all word nodes within this range. Whenever the value for freq_lex is set to one, the related word and the verse it is part of are reported as a *hapax legomenon*. The indicated verse is hyperlinked to the STEP Bible, allowing for easy review of the verse. Clicking on the Hebrew word will bring you to the relevant Hebrew verse in Bible Online Learner (BibleOL). The last three columns provide additional information regarding the type and function of the word.

In [4]:
# find all word nodes for this parasha (we can either use the transliterated name or the sequence number)
parashaQuery = '''
verse parashanum=5
  word
'''
parashaResults = BHSA.search(parashaQuery)

  0.26s 1972 results


In [5]:
# Store parashname, start and end verse for future use
startNode=parashaResults[0][0]
endNode=parashaResults[-1][0]
parashaNameHebrew=F.parashahebr.v(startNode)
parashaNameEnglish=F.parashatrans.v(startNode)
bookStart,chapterStart,startVerse=T.sectionFromNode(startNode)
parashaStart=f'{bookStart} {chapterStart}:{startVerse}'
bookEnd,chapterEnd,startEnd=T.sectionFromNode(endNode)
parashaEnd=f'{chapterEnd}:{startEnd}'

def wrapHTML(body, title):
    output = (
        f'<html><head><title>{title}</title></head>'
        f'<body>{body}<p>Data generated by `hapax.ipynb` at ' 
        '`<a href="https://github.com/tonyjurg/Parashot" target="_blank">'
        'github.com/tonyjurg/Parashot</a>`</p></body></html>'
    )
    return output

The following cell contains code that allows us to provide additional information in the table **as it is annotated in the BHSA dataset**. See also the caution on feature [nametype](https://github.com/ETCBC/bhsa/blob/master/docs/features/nametype.md): 
> It is unclear how completely and correctly this feature has been assigned.

In [6]:
# part of speech expantion table 
# https://github.com/ETCBC/bhsa/blob/master/docs/features/sp.md
posMapping= {
    # "abreviation" (key) : "description"
    'art':	'article',
    'verb':	'verb',
    'subs':	'noun',
    'nmpr':	'proper noun',
    'advb':	'adverb',
    'prep':	'preposition',
    'conj':	'conjunction',
    'prps':	'personal pronoun',
    'prde':	'demonstrative pronoun',
    'prin':	'interrogative pronoun',
    'intj':	'interjection',
    'nega':	'negative particle',
    'inrg':	'interrogative particle',
    'adjv':	'adjective'
}

# Subclassification of part of speech (feature ls on word and lex nodes)
# https://github.com/ETCBC/bhsa/blob/master/docs/features/ls.md
subclassMapping = {
    # "abreviation" (key) : "description"
    'nmdi':	'distributive noun',
    'nmcp':	'copulative noun',
    'padv':	'potential adverb',
    'afad':	'anaphoric adverb',
    'ppre':	'potential preposition',
    'cjad':	'conjunctive adverb',
    'ordn':	'ordinal',
    'vbcp':	'copulative verb',
    'mult':	'noun of multitude',
    'focp':	'focus particle',
    'ques':	'interrogative particle',
    'gntl':	'gentilic',
    'quot':	'quotation verb',
    'card':	'cardinal',
    'none': ''
}

# expand information in feature nametype (a comma separated list)
# https://github.com/ETCBC/bhsa/blob/master/docs/features/nametype.md
nametypeExpantions = {
    'pers':	'person',
    'mens':	'measurement unit',
    'gens':	'people',
    'topo':	'place',
    'ppde':	'demonstrative personal pronoun'
}
def expandNametype(inputText):
    outputText = inputText
    if inputText is not None:
        for old, new in nametypeExpantions.items():
            outputText = outputText.replace(old, new)
    return outputText

The following cell performs the actual gathering of the hapax legomena:

In [7]:
from IPython.display import HTML, display

def escapeMarkdown(text):
    return text.replace("<", "&lt;").replace(">", "&gt;") if text is not None else ""

# Initialize HTML content
reportTitle=f'Hapax Legomena for parasha {parashaNameEnglish} ({parashaStart}-{parashaEnd})'
htmlContent = f"<h2>{reportTitle}</h2>"
htmlContent += "<table border='1' style='border-collapse: collapse; width: 100%;'>"
htmlContent += "<tr><th>Verse</th><th>Hebrew Word</th><th>English Gloss</th><th>Part of Speech</th><th>Subclass</th><th>Name Type</th></tr>"

numberOfHapax = 0

# Generate table rows
for verse, node in parashaResults:
    freq = F.freq_lex.v(node)
    if freq == 1:
        numberOfHapax += 1
        sectionTuple = T.sectionFromNode(node)
        wordLink = (
            f"<a href=\"https://learner.bible/text/show_text/ETCBC4/"
            f"{sectionTuple[0]}/{sectionTuple[1]}/{sectionTuple[2]}\" "
            f"target=\"_blank\">{F.g_word_utf8.v(node)}</a>"
        )
        linkSTEPbible = (
            f"<a href=\"https://www.stepbible.org/?q=version=NASB2020&"
            f"reference={sectionTuple[0]}.{sectionTuple[1]}:{sectionTuple[2]}&options=HNVUG\" "
            f"target=\"_blank\">{sectionTuple[0]} {sectionTuple[1]}:{sectionTuple[2]}</a>"
        )
        htmlContent += (
            f"<tr>"
            f"<td>{linkSTEPbible}</td>"
            f"<td>{wordLink}</td>"
            f"<td>{escapeMarkdown(F.gloss.v(node))}</td>"
            f"<td>{escapeMarkdown(posMapping.get(F.sp.v(node), ''))}</td>"
            f"<td>{escapeMarkdown(subclassMapping.get(F.ls.v(node), ''))}</td>"
            f"<td>{escapeMarkdown(expandNametype(F.nametype.v(node)))}</td>"
            f"</tr>"
        )

# Close the table
htmlContent += "</table>"
htmlContent += f"<p>{numberOfHapax} hapaxes found.</p>"


# Display the HTML content in the notebook
display(HTML(htmlContent))

# Define the HTML filename and store to file
fileName = f"hapax_legomena({parashaNameEnglish.replace(' ','_')}).html"
htmlContentFull = wrapHTML(htmlContent,reportTitle)
with open(fileName, "w", encoding="utf-8") as file:
    file.write(htmlContentFull)
    
# display download button
downloadButton = f"""
<a download="{fileName}" href="data:text/html;charset=utf-8,{htmlContentFull.replace('&', '&amp;').replace('<', '&lt;').replace('>', '&gt;').replace('"', '&quot;').replace("'", '&#39;')}" target="_blank">
    <button>Download as HTML</button>
</a>
"""
display(HTML(downloadButton))

# 4 - Required libraries <a class="anchor" id="bullet4"></a>
##### [Back to ToC](#TOC)

The scripts in this notebook require (beside `text-fabric`) the following Python libraries to be installed in the environment:

    IPython

You can install any missing library from within Jupyter Notebook using either`pip` or `pip3`.

# 5 - Further reading <a class="anchor" id="bullet5"></a>
##### [Back to ToC](#TOC)

An discussion regarding Hapax Legomena, including details about ten hapaxes in the Hebrew Bible can be found at [The Torah.com](https://www.thetorah.com/article/hapax-legomena-ten-biblical-examples).

# 6 - Notebook version details<a class="anchor" id="bullet6"></a>
##### [Back to ToC](#TOC)

<div style="float: left;">
  <table>
    <tr>
      <td><strong>Author</strong></td>
      <td>Tony Jurg</td>
    </tr>
    <tr>
      <td><strong>Version</strong></td>
      <td>1.2</td>
    </tr>
    <tr>
      <td><strong>Date</strong></td>
      <td>18 November 2024</td>
    </tr>
  </table>
</div>